In [1]:
from pathlib import Path
data_path = Path('./datasets_knowledge_embedding')
data_path.mkdir(exist_ok=True)

!cd $data_path && git clone https://github.com/villmow/datasets_knowledge_embedding src

fatal: destination path 'src' already exists and is not an empty directory.


In [4]:
import sys
sys.path.append('../')

In [6]:
from catlearn.tensor_utils import subproba_kl_div, Tsor
from catlearn.graph_utils import DirectedGraph
from catlearn.composition_graph import CompositeArrow
from catlearn.categorical_model import (
    RelationModel, ScoringModel, RelationCache,
    DecisionCatModel, TrainableDecisionCatModel)
from catlearn.algebra_models import (
    Algebra, VectAlgebra, MatrixAlgebra, AffineAlgebra)

In [16]:
# WN18 train dataset
with open('./datasets_knowledge_embedding/src/WN18/text/train.txt') as f:
    data_triples = [line.split('\t') for line in f.read().splitlines()]
    
# get the set of all possible tags in train dataset
tags = frozenset(triple[1] for triple in data_triples)

frozenset({'_has_part', '_derivationally_related_form', '_verb_group', '_hyponym', '_part_of', '_instance_hypernym', '_similar_to', '_synset_domain_topic_of', '_synset_domain_region_of', '_synset_domain_usage_of', '_also_see', '_member_of_domain_usage', '_member_of_domain_topic', '_member_holonym', '_instance_hyponym', '_hypernym', '_member_of_domain_region', '_member_meronym'})


In [19]:
train_graph = DirectedGraph()
for (source, tag, target) in data_triples:
    if train_graph.has_edge(source ,target):
        train_graph[source][target][tag] = True
    else:
        train_graph.add_edge(source, target, **{tag: True})

In [20]:
train_graph

DirectedGraph(plaything.n.01 > {'swing.n.02': {'_hyponym': True}, 'seesaw.n.01': {'_hyponym': True}, 'slingshot.n.01': {'_hyponym': True}, 'doll.n.01': {'_hyponym': True}, 'artifact.n.01': {'_hypernym': True}, 'sandbox.n.02': {'_hyponym': True}, 'play.v.16': {'_derivationally_related_form': True}, 'water_pistol.n.01': {'_hyponym': True}, 'top.n.08': {'_hyponym': True}, 'kite.n.03': {'_hyponym': True}, 'slide.n.04': {'_hyponym': True}}, swing.n.02 > {'dangle.v.01': {'_derivationally_related_form': True}, 'playground.n.02': {'_part_of': True}, 'plaything.n.01': {'_hypernym': True}, 'mechanical_device.n.01': {'_hypernym': True}}, land_reform.n.01 > {'reform.n.01': {'_hypernym': True}, 'government.n.02': {'_synset_domain_topic_of': True}}, reform.n.01 > {'reform.v.01': {'_derivationally_related_form': True}, 'improvement.n.02': {'_hypernym': True}, 'reform.v.05': {'_derivationally_related_form': True}, 'land_reform.n.01': {'_hyponym': True}}, nematocera.n.01 > {'diptera.n.01': {'_member_ho